# New youga class in Toronto

### Introduction

From [here](https://www.thegoodbody.com/yoga-statistics/) we can find out that Yoga has grown massively in popularity over the past few years, with passionate yogis stretching around the world. The facts show that it has many health benefits, particularly for those suffering from back pain, and with the spend on yoga products growing annually the trend shows no sign of slowing down.
Also yoga market has massive annual spends Worldwide each year. 
So it's interesting trend and we can participate in it.

### Task

Need to find a good place for creating new yoga class in Toronto. Based on different open data source we should find on which attributes of Neighbourhoods have more influence on yoga studios and where is the best place for it, depending of base surroundings.

### How data sould be used

1. As it is told [here](https://www.thegoodbody.com/yoga-statistics/) yoga is popular for certain segments of the population. We should try to get this statistics from Neighbourhood Profiles 2016 (data source 1). This source includes demographical, social, employment data for each Neighbourhood. I plan select: Total population, Age (different groups), Sex (different groups), Marital status, Education, Employment status
2. After that we take data from Foursquare (data source 2) and find out which parameters affects on yoga studios in thease neighbourhoods and find out which parameters affects on Yoga studios mostly and where yoga studios os not enough.
3. We also should find best neighbours (fithes studios, health bars and so on) for yoga studios from Foursquare 
4. After that we can merge data from goverment statistics and best neighbours of yoga studios and find the places where new studio should be.
5. Find out existance of yoga studios in that Neighbourhood and define can we place another one or not

#### Data sources

1. Neighbourhood Profiles 2016 (CSV) https://www.toronto.ca/city-government/data-research-maps/open-data/open-data-catalogue/locations-and-mapping/#8c732154-5012-9afe-d0cd-ba3ffc813d5a
2. Foursquare.com


## Realisation

In [1]:
import pandas as pd
import numpy as np

##### Load data

In [2]:
!wget -q -O 'TorrontoData.csv' https://www.toronto.ca/ext/open_data/catalog/data_set_files/2016_neighbourhood_profiles.csv

In [3]:
TorrontoCsv = pd.read_csv('TorrontoData.csv',encoding = 'unicode_escape')
TorrontoCsv.drop(['Topic','Category','Data Source'], axis=1, inplace=True)
TorrontoCsv.rename(columns={"Characteristic": "Idx"},inplace=True)
TorrontoCsv.set_index('Idx',inplace = True)

#### Saving Neighbourhood Numbers

In [4]:
TorrontoNeighbourhood = TorrontoCsv.filter(regex='Neighbourhood Number', axis=0).transpose()[1:]
TorrontoNeighbourhood.head()

Idx                          Neighbourhood Number
Agincourt North                               129
Agincourt South-Malvern West                  128
Alderwood                                      20
Annex                                          95
Banbury-Don Mills                              42

In [5]:
TorrontoCsv.dropna(axis=0,inplace=True)
TorrontoCsv.head()

City of Toronto Agincourt North  \
Idx                                                                             
Population, 2016                                    2,731,571          29,113   
Population, 2011                                    2,615,060          30,279   
Population Change 2011-2016                             4.50%          -3.90%   
Total private dwellings                             1,179,057           9,371   
Private dwellings occupied by usual residents       1,112,929           9,120   

                                              Agincourt South-Malvern West  \
Idx                                                                          
Population, 2016                                                    23,757   
Population, 2011                                                    21,988   
Population Change 2011-2016                                          8.00%   
Total private dwellings                                              8,535   
Private dwellings occupied by usual residents                        8,136   

                                              Alderwood   Annex  \
Idx                                                               
Population, 2016                                 12,054  30,526   
Population, 2011                                 11,904  29,177   
Population Change 2011-2016                       1.30%   4.60%   
Total private dwellings                           4,732  18,109   
Private dwellings occupied by usual residents     4,616  15,934   

                                              Banbury-Don Mills  \
Idx                                                               
Population, 2016                                         27,695   
Population, 2011                                         26,918   
Population Change 2011-2016                               2.90%   
Total private dwellings                                  12,473   
Private dwellings occupied by usual residents            12,124   

                                              Bathurst Manor  \
Idx                                                            
Population, 2016                                      15,873   
Population, 2011                                      15,434   
Population Change 2011-2016                            2.80%   
Total private dwellings                                6,418   
Private dwellings occupied by usual residents          6,089   

                                              Bay Street Corridor  \
Idx                                                                 
Population, 2016                                           25,797   
Population, 2011                                           19,348   
Population Change 2011-2016                                33.30%   
Total private dwellings                                    18,436   
Private dwellings occupied by usual residents              15,074   

                                              Bayview Village  \
Idx                                                             
Population, 2016                                       21,396   
Population, 2011                                       17,671   
Population Change 2011-2016                            21.10%   
Total private dwellings                                10,111   
Private dwellings occupied by usual residents           9,532   

                                              Bayview Woods-Steeles  ...  \
Idx                                                                  ...   
Population, 2016                                             13,154  ...   
Population, 2011                                             13,530  ...   
Population Change 2011-2016                                  -2.80%  ...   
Total private dwellings                                       4,895  ...   
Private dwellings occupied by usual residents                 4,698  ...   

                                              Willowdale West  \
Idx 

##### For consistency, ensure that all column labels of type string.

In [6]:
all(isinstance(column, str) for column in TorrontoCsv.columns)

True

#### Convert to numbers

In [7]:
TorrontoCsv.replace("%",'', regex=True,inplace = True)
TorrontoCsv.replace(",",'', regex=True,inplace = True)
TorrontoCsv=TorrontoCsv.apply(pd.to_numeric, errors='coerce').fillna(0)

##### Filtering data data

In [8]:
TorrontoFilteredData=pd.concat([
                        TorrontoCsv.filter(regex='^Male:', axis=0),
                        TorrontoCsv.filter(regex='^Female:', axis=0),
                        TorrontoCsv.filter(regex='Married or living common law', axis=0),
                        TorrontoCsv.filter(regex='Not married and not living common law', axis=0),
                        TorrontoCsv.filter(regex='No certificate, diploma or degree', axis=0).head(1),
                        TorrontoCsv.filter(regex='Secondary \(high\) school diploma or equivalency certificate', axis=0).head(1),
                        TorrontoCsv.filter(regex='Postsecondary certificate, diploma or degree', axis=0).head(1),
                        TorrontoCsv.filter(regex='Employed$', axis=0),
                        TorrontoCsv.filter(regex='Unemployed$', axis=0)
])


#### Change from values to relative

In [9]:
col = TorrontoFilteredData.columns[1:]
clmn = list(col) 
for i in clmn: 
    TorrontoFilteredData[i]=TorrontoFilteredData[i] / TorrontoFilteredData['City of Toronto']
TorrontoFilteredData.drop(['City of Toronto'], axis=1, inplace=True)  
TorrontoFilteredData.head(3)

Agincourt North  Agincourt South-Malvern West  \
Idx                                                                   
Male: 0 to 04 years          0.009443                      0.008227   
Male: 05 to 09 years         0.010022                      0.007787   
Male: 10 to 14 years         0.010162                      0.007083   

                      Alderwood     Annex  Banbury-Don Mills  Bathurst Manor  \
Idx                                                                            
Male: 0 to 04 years    0.005151  0.006367           0.008155        0.006224   
Male: 05 to 09 years   0.003893  0.005263           0.009517        0.005119   
Male: 10 to 14 years   0.003464  0.005004           0.010393        0.006390   

                      Bay Street Corridor  Bayview Village  \
Idx                                                          
Male: 0 to 04 years              0.006724         0.006510   
Male: 05 to 09 years             0.003317         0.005696   
Male: 10 to 14 years             0.002002         0.006313   

                      Bayview Woods-Steeles  Bedford Park-Nortown  ...  \
Idx                                                                ...   
Male: 0 to 04 years                0.002933              0.009657  ...   
Male: 05 to 09 years               0.003749              0.011464  ...   
Male: 10 to 14 years               0.004927              0.013550  ...   

                      Willowdale West  Willowridge-Martingrove-Richview  \
Idx                                                                       
Male: 0 to 04 years          0.005079                          0.008870   
Male: 05 to 09 years         0.004470                          0.009012   
Male: 10 to 14 years         0.004080                          0.009393   

                        Woburn  Woodbine Corridor  Woodbine-Lumsden  Wychwood  \
Idx                                                                             
Male: 0 to 04 years   0.023249           0.006581          0.003219  0.004650   
Male: 05 to 09 years  0.024585           0.005768          0.002596  0.005047   
Male: 10 to 14 years  0.024636           0.005081          0.002772  0.004773   

                      Yonge-Eglinton  Yonge-St.Clair  York University Heights  \
Idx                                                                             
Male: 0 to 04 years         0.004292        0.003148                 0.010802   
Male: 05 to 09 years        0.004398        0.003172                 0.009877   
Male: 10 to 14 years        0.004311        0.003003                 0.009778   

                      Yorkdale-Glen Park  
Idx                                       
Male: 0 to 04 years             0.004578  
Male: 05 to 09 years            0.004542  
Male: 10 to 14 years            0.005697  

[3 rows x 140 columns]

#### Transpose data and get result

In [10]:
TorrontoData=TorrontoFilteredData.transpose()

##### Get result DataFrame

In [11]:
TorrontoData.reset_index(inplace=True)
TorrontoData.rename(columns={"index": "Neighbourhood"},inplace=True)
TorrontoData.head()

Idx                 Neighbourhood  Male: 0 to 04 years  Male: 05 to 09 years  \
0                 Agincourt North             0.009443              0.010022   
1    Agincourt South-Malvern West             0.008227              0.007787   
2                       Alderwood             0.005151              0.003893   
3                           Annex             0.006367              0.005263   
4               Banbury-Don Mills             0.008155              0.009517   

Idx  Male: 10 to 14 years  Male: 15 to 19 years  Male: 20 to 24 years  \
0                0.010162              0.011315              0.010419   
1                0.007083              0.010506              0.010265   
2                0.003464              0.003839              0.003644   
3                0.005004              0.006263              0.012472   
4                0.010393              0.009631              0.007186   

Idx  Male: 25 to 29 years  Male: 30 to 34 years  Male: 35 to 39 years  \
0                0.008911              0.007668              0.007229   
1                0.009174              0.007530              0.006644   
2                0.003117              0.003765              0.004837   
3                0.018261              0.014785              0.011215   
4                0.005663              0.006750              0.007813   

Idx  Male: 40 to 44 years  ...  Female: 90 to 94 years  \
0                0.008783  ...                0.011852   
1                0.007049  ...                0.007407   
2                0.004854  ...                0.005185   
3                0.009649  ...                0.019259   
4                0.009418  ...                0.026667   

Idx  Female: 95 to 99 years  Female: 100 years and over  \
0                  0.017266                    0.015385   
1                  0.005755                    0.000000   
2                  0.001439                    0.007692   
3                  0.025899                    0.038462   
4                  0.030216                    0.030769   

Idx    Married or living common law    Not married and not living common law  \
0                          0.012020                                 0.009613   
1                          0.009485                                 0.008224   
2                          0.004855                                 0.003949   
3                          0.010391                                 0.013793   
4                          0.011207                                 0.009418   

Idx    No certificate, diploma or degree  \
0                               0.017358   
1                               0.010693   
2                               0.005314   
3                               0.004200   
4                               0.006082   

Idx    Secondary (high) school diploma or equivalency certificate  \
0                                             0.013296              
1                                             0.010854              
2                                             0.005275              
3                                             0.007610              
4                                             0.009179              

Idx    Postsecondary certificate, diploma or degree      Employed  \
0                                          0.008099      0.009189   
1                                          0.007583      0.007974   
2                                          0.003908      0.004705   
3                                          0.015062      0.012711   
4                                          0.011759      0.009557   

Idx      Unemployed  
0          0.011120  
1          0.009689  
2          0.003393  
3          0.010220  
4          0.008258  

[5 rows x 50 columns]

In [12]:
TorrontoData.set_index('Neighbourhood').join(TorrontoNeighbourhood, lsuffix='_caller', rsuffix='_other')

Idx                                Male: 0 to 04 years  Male: 05 to 09 years  \
Neighbourhood                                                                  
Agincourt North                               0.009443              0.010022   
Agincourt South-Malvern West                  0.008227              0.007787   
Alderwood                                     0.005151              0.003893   
Annex                                         0.006367              0.005263   
Banbury-Don Mills                             0.008155              0.009517   
Bathurst Manor                                0.006224              0.005119   
Bay Street Corridor                           0.006724              0.003317   
Bayview Village                               0.006510              0.005696   
Bayview Woods-Steeles                         0.002933              0.003749   
Bedford Park-Nortown                          0.009657              0.011464   
Beechborough-Greenbrook                       0.002575              0.002812   
Bendale                                       0.011017              0.011391   
Birchcliffe-Cliffside                         0.008155              0.008363   
Black Creek                                   0.010659              0.011536   
Blake-Jones                                   0.003863              0.003533   
Briar Hill-Belgravia                          0.004936              0.004542   
Bridle Path-Sunnybrook-York Mills             0.002575              0.003461   
Broadview North                               0.004221              0.003605   
Brookhaven-Amesbury                           0.007583              0.008796   
Cabbagetown-South St. James Town              0.002218              0.001947   
Caledonia-Fairbank                            0.003863              0.003461   
Casa Loma                                     0.002647              0.003028   
Centennial Scarborough                        0.004435              0.005119   
Church-Yonge Corridor                         0.004864              0.002235   
Clairlea-Birchmount                           0.011446              0.010887   
Clanton Park                                  0.007297              0.007498   
Cliffcrest                                    0.005437              0.006417   
Corso Italia-Davenport                        0.005294              0.004903   
Danforth                                      0.004650              0.004470   
Danforth East York                            0.008727              0.007354   
...                                                ...                   ...   
South Riverdale                               0.012876              0.009877   
St.Andrew-Windfields                          0.004721              0.007210   
Steeles                                       0.007654              0.008363   
Stonegate-Queensway                           0.010158              0.011103   
Tam O'Shanter-Sullivan                        0.009800              0.009805   
Taylor-Massey                                 0.008012              0.008075   
The Beaches                                   0.009300              0.009589   
Thistletown-Beaumond Heights                  0.003791              0.004326   
Thorncliffe Park                              0.014236              0.015285   
Trinity-Bellwoods                             0.005079              0.004542   
University                                    0.001645              0.001226   
Victoria Village                              0.006438              0.006921   
Waterfront Communities-The Island             0.015452              0.006705   
West Hill                                     0.010730              0.011536   
West Humber-Clairville                        0.011446              0.013194   
Westminster-Branson                           0.009300              0.008075   
Weston                                        0.007797              0.008147   


### Getting Toronto coordinates

In [13]:
!pip install folium
import folium # map rendering library
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

     |████████████████████████████████| 92kB 19.3MB/s eta 0:00:01


In [14]:
address = 'Toronto'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.653963, -79.387207.


In [16]:
import json
import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

In [17]:
topo = f'https://raw.githubusercontent.com/smtkvb/Python_Coursera_Capstone/master/toronto_topo.json'


m = folium.Map(location=[latitude, longitude], zoom_start=11)


folium.TopoJson(
    json.loads(requests.get(topo).text),
    'objects.toronto',
    name='topojson'
).add_to(m)

folium.LayerControl().add_to(m)

m


### Getting geo polygon data as DF

Why this is for:
1. Need to find centre of each Neighbourhood. After that I goona use it for getting data from foursquare
2. Need to combine kind of polynom object to check, that venue from foursquare really from this Neighbourhood 

In [141]:
# This one is geojson from the same source as it were topojson
geojson = f'https://raw.githubusercontent.com/smtkvb/Python_Coursera_Capstone/master/toronto_crs84.geojson'


In [139]:
from urllib.request import urlopen
import json
from pandas.io.json import json_normalize

response = urlopen(geojson)
elevations = response.read()
data = json.loads(elevations)
geo_df=json_normalize(data['features'])
geo_df.head()

geometry.coordinates geometry.type  \
0  [[[-79.39119482699992, 43.68108112399995], [-7...       Polygon   
1  [[[-79.50528791599992, 43.759873493999955], [-...       Polygon   
2  [[[-79.43998431099992, 43.761557654999955], [-...       Polygon   
3  [[[-79.43968732599991, 43.70560981799996], [-7...       Polygon   
4  [[[-79.49262119699992, 43.6474363499999], [-79...       Polygon   

           properties.AREA_NAME properties.AREA_S_CD     type  
0           Yonge-St.Clair (97)                  097  Feature  
1  York University Heights (27)                  027  Feature  
2         Lansing-Westgate (38)                  038  Feature  
3       Yorkdale-Glen Park (31)                  031  Feature  
4      Stonegate-Queensway (16)                  016  Feature

In [140]:
geo_df.rename(columns={"geometry.coordinates": "coordinates", "properties.AREA_NAME": "Neighbourghood", "properties.AREA_S_CD": "id"},inplace=True)

#### Function for centre of district

In [134]:
def GetCentre(d) :
    x,y=zip(*d)
    center=(max(x)+min(x))/2., (max(y)+min(y))/2.
    return(center)

In [151]:
from matplotlib.path import Path
geo_df['coordinates'].iloc[0]
geo_df['Poligon'] = geo_df.apply(lambda row: Path(row.coordinates[0]), axis=1)
geo_df['Centre'] = geo_df.apply(lambda row: GetCentre(row.coordinates[0]), axis=1)
geo_df.head()

coordinates geometry.type  \
0  [[[-79.39119482699992, 43.68108112399995], [-7...       Polygon   
1  [[[-79.50528791599992, 43.759873493999955], [-...       Polygon   
2  [[[-79.43998431099992, 43.761557654999955], [-...       Polygon   
3  [[[-79.43968732599991, 43.70560981799996], [-7...       Polygon   
4  [[[-79.49262119699992, 43.6474363499999], [-79...       Polygon   

                 Neighbourghood   id     type    a  \
0           Yonge-St.Clair (97)  097  Feature  108   
1  York University Heights (27)  027  Feature  108   
2         Lansing-Westgate (38)  038  Feature  108   
3       Yorkdale-Glen Park (31)  031  Feature  108   
4      Stonegate-Queensway (16)  016  Feature  108   

                                             Poligon  \
0  Path(array([[-79.39119483,  43.68108112],\n   ...   
1  Path(array([[-79.50528792,  43.75987349],\n   ...   
2  Path(array([[-79.43998431,  43.76155765],\n   ...   
3  Path(array([[-79.43968733,  43.70560982],\n   ...   
4  Path(array([[-79.4926212 ,  43.64743635],\n   ...   

                                    Centre  
0  (-79.39853901899993, 43.68808772449996)  
1   (-79.4922534984999, 43.76490100749996)  
2  (-79.42441129199992, 43.75211632699995)  
3  (-79.45555520499992, 43.71487854199995)  
4  (-79.49884145449992, 43.63527967899996)

#### Example of coordinates check

In [116]:
venue=[[-79.397842,43.690523]]
p = Path(geo_df['coordinates'].iloc[0][0]) 
p.contains_points(venue)

array([ True])

### Getting date from foursquare

In [159]:
# The code was removed by Watson Studio for sharing.

In [160]:
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 3000 # define radius 3km
categoryId='4bf58dd8d48988d102941735'# yoga centre



In [164]:
from time import sleep
d=[]
for index, row in geo_df.iterrows():  
    url = 'https://api.foursquare.com/v2/venues/search?&client_id={}&client_secret={}&v={}&near={},{}&radius={}&limit={}&categoryId={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    geo_df['Centre'][index][1], 
    geo_df['Centre'][index][0], 
    radius, 
    LIMIT,
    categoryId)
    results = requests.get(url).json()    
    d.append({'Venues' : results, 'id':geo_df['id'][index]})

AttributeError: 'list' object has no attribute 'head'

In [167]:
pd.DataFrame(d).head()

Venues   id
0  {'meta': {'code': 200, 'requestId': '5d2b5184f...  097
1  {'meta': {'code': 200, 'requestId': '5d2b51866...  027
2  {'meta': {'code': 200, 'requestId': '5d2b51893...  038
3  {'meta': {'code': 200, 'requestId': '5d2b518b9...  031
4  {'meta': {'code': 200, 'requestId': '5d2b518d6...  016

In [178]:
geo_df=geo_df.set_index('id').join(pd.DataFrame(d).set_index('id'))

In [384]:
venuesList=pd.DataFrame()
for index, row in geo_df.iterrows(): 
    responce = row['Venues']['response']
    if 'venues' in responce:
        venues=responce['venues']
        if venues and 'name' in venues[0]:
            nearby_venues = json_normalize(venues) # flatten JSON
            temp=nearby_venues[['name','location.lat','location.lng']]
            temp.insert(0, 'id', index) 
            temp.insert(4, 'poligon', row.Poligon) 
            
            venuesList=venuesList.append(temp, ignore_index=True)
venuesList.columns = [col.split(".")[-1] for col in venuesList.columns]            
venuesList.head()


id                            name        lat        lng  \
0  097              Moksha Yoga Uptown  43.688799 -79.394484   
1  097  Noor Light Healing Arts Studio  43.665129 -79.410511   
2  097               Rainbow Body Yoga  43.664529 -79.380073   
3  097                   House Of Yoga  43.663780 -79.417956   
4  097                  eMbody Fitness  43.703813 -79.412895   

                                             poligon  
0  Path(array([[-79.39119483,  43.68108112],\n   ...  
1  Path(array([[-79.39119483,  43.68108112],\n   ...  
2  Path(array([[-79.39119483,  43.68108112],\n   ...  
3  Path(array([[-79.39119483,  43.68108112],\n   ...  
4  Path(array([[-79.39119483,  43.68108112],\n   ...

In [441]:
def myfunc(lat, lng, poligon):
    venue=[[lng,lat]]
    return poligon.contains_points(venue)

#### Filtered list of yoga studios for each Neighbourhood and grouped then into Neighbourghood's table and geodata table

In [469]:
filteredvenuesList= venuesList[ venuesList.apply(lambda x: ~myfunc(x.lat,x.lng,x.poligon)[0], axis=1) ]
filteredvenuesList['id'] = filteredvenuesList['id'].astype(int)

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app


In [473]:
geo_df=geo_df.join(filteredvenuesList.groupby(['id']).count().rename(columns={'name':'VenueCount'})['VenueCount']).fillna(0)
TorrontoData=TorrontoData.join(filteredvenuesList.groupby(['id']).count().rename(columns={'name':'VenueCount'})['VenueCount']).fillna(0)

In [474]:
TorrontoData.head()

Neighbourhood  Male: 0 to 04 years  Male: 05 to 09 years  \
0               Agincourt North             0.009443              0.010022   
1  Agincourt South-Malvern West             0.008227              0.007787   
2                     Alderwood             0.005151              0.003893   
3                         Annex             0.006367              0.005263   
4             Banbury-Don Mills             0.008155              0.009517   

   Male: 10 to 14 years  Male: 15 to 19 years  Male: 20 to 24 years  \
0              0.010162              0.011315              0.010419   
1              0.007083              0.010506              0.010265   
2              0.003464              0.003839              0.003644   
3              0.005004              0.006263              0.012472   
4              0.010393              0.009631              0.007186   

   Male: 25 to 29 years  Male: 30 to 34 years  Male: 35 to 39 years  \
0              0.008911              0.007668              0.007229   
1              0.009174              0.007530              0.006644   
2              0.003117              0.003765              0.004837   
3              0.018261              0.014785              0.011215   
4              0.005663              0.006750              0.007813   

   Male: 40 to 44 years  ...  Female: 95 to 99 years  \
0              0.008783  ...                0.017266   
1              0.007049  ...                0.005755   
2              0.004854  ...                0.001439   
3              0.009649  ...                0.025899   
4              0.009418  ...                0.030216   

   Female: 100 years and over    Married or living common law  \
0                    0.015385                        0.012020   
1                    0.000000                        0.009485   
2                    0.007692                        0.004855   
3                    0.038462                        0.010391   
4                    0.030769                        0.011207   

     Not married and not living common law  \
0                                 0.009613   
1                                 0.008224   
2                                 0.003949   
3                                 0.013793   
4                                 0.009418   

     No certificate, diploma or degree  \
0                             0.017358   
1                             0.010693   
2                             0.005314   
3                             0.004200   
4                             0.006082   

     Secondary (high) school diploma or equivalency certificate  \
0                                           0.013296              
1                                           0.010854              
2                                           0.005275              
3                                           0.007610              
4                                           0.009179              

     Postsecondary certificate, diploma or degree      Employed  \
0                                        0.008099      0.009189   
1                                        0.007583      0.007974   
2                                        0.003908      0.004705   
3                                        0.015062      0.012711   
4                                        0.011759      0.009557   

       Unemployed  VenueCount  
0        0.011120         0.0  
1        0.009689         0.0  
2        0.003393         2.0  
3        0.010220         1.0  
4        0.008258         1.0  

[5 rows x 51 columns]

In [521]:
geo_df.head()

coordinates geometry.type  \
id                                                                     
097  [[[-79.39119482699992, 43.68108112399995], [-7...       Polygon   
027  [[[-79.50528791599992, 43.759873493999955], [-...       Polygon   
038  [[[-79.43998431099992, 43.761557654999955], [-...       Polygon   
031  [[[-79.43968732599991, 43.70560981799996], [-7...       Polygon   
016  [[[-79.49262119699992, 43.6474363499999], [-79...       Polygon   

                   Neighbourghood     type  \
id                                           
097           Yonge-St.Clair (97)  Feature   
027  York University Heights (27)  Feature   
038         Lansing-Westgate (38)  Feature   
031       Yorkdale-Glen Park (31)  Feature   
016      Stonegate-Queensway (16)  Feature   

                                               Poligon  \
id                                                       
097  Path(array([[-79.39119483,  43.68108112],\n   ...   
027  Path(array([[-79.50528792,  43.75987349],\n   ...   
038  Path(array([[-79.43998431,  43.76155765],\n   ...   
031  Path(array([[-79.43968733,  43.70560982],\n   ...   
016  Path(array([[-79.4926212 ,  43.64743635],\n   ...   

                                      Centre  \
id                                             
097  (-79.39853901899993, 43.68808772449996)   
027   (-79.4922534984999, 43.76490100749996)   
038  (-79.42441129199992, 43.75211632699995)   
031  (-79.45555520499992, 43.71487854199995)   
016  (-79.49884145449992, 43.63527967899996)   

                                                Venues  VenueCount  
id                                                                  
097  {'meta': {'code': 200, 'requestId': '5d2b5184f...        47.0  
027  {'meta': {'code': 200, 'requestId': '5d2b51866...         1.0  
038  {'meta': {'code': 200, 'requestId': '5d2b51893...         9.0  
031  {'meta': {'code': 200, 'requestId': '5d2b518b9...         3.0  
016  {'meta': {'code': 200, 'requestId': '5d2b518d6...        11.0

In [561]:
geo_json_data = json.loads(requests.get(geojson).text)

m = folium.Map(location=[latitude, longitude], zoom_start=11)

folium.GeoJson(geo_json_data).add_to(m)

m

In [541]:
from branca.colormap import linear

colormap = linear.YlGn_09.scale(
    geo_df.VenueCount.min(),
    geo_df.VenueCount.max())

print(colormap(5.0))

colormap

#f9fdc1


In [542]:
topo = f'https://raw.githubusercontent.com/smtkvb/Python_Coursera_Capstone/master/toronto_topo.json'

geo_df_dict=  geo_df['VenueCount']

m = folium.Map(location=[latitude, longitude], zoom_start=11)


folium.TopoJson(
    json.loads(requests.get(topo).text),
    'objects.toronto',
    name='topojson',
    style_function=lambda feature: {
        'fillColor': colormap(geo_df_dict[feature['id']]),
        'color': 'black',
        'weight': 1,
        'dashArray': '5, 5',
        'fillOpacity': 0.9,
    }
).add_to(m)

folium.LayerControl().add_to(m)

m


KeyError: 'id'

In [553]:

geo_json_data = json.loads(requests.get(geojson).text)
geo_json_data

{'type': 'FeatureCollection',
 'crs': {'type': 'name',
  'properties': {'name': 'urn:ogc:def:crs:OGC:1.3:CRS84'}},
 'features': [{'type': 'Feature',
   'properties': {'AREA_S_CD': '097', 'AREA_NAME': 'Yonge-St.Clair (97)'},
   'geometry': {'type': 'Polygon',
    'coordinates': [[[-79.39119482699992, 43.68108112399995],
      [-79.39140543199991, 43.68096955399996],
      [-79.39322377799992, 43.68016563999995],
      [-79.39580883199991, 43.67897993999995],
      [-79.39734938999993, 43.67827481299995],
      [-79.39745605399992, 43.67822540699995],
      [-79.39756389799992, 43.67816700199996],
      [-79.39767131899993, 43.67811759699996],
      [-79.39777954499992, 43.678068201999956],
      [-79.39788853599991, 43.678014288999954],
      [-79.39793136699991, 43.67799495999996],
      [-79.39794405299993, 43.67802629499996],
      [-79.39801215899993, 43.678203873999955],
      [-79.39814090099992, 43.678530735999956],
      [-79.39835150999991, 43.679039164999956],
      [-79.39856

In [554]:
url = 'https://raw.githubusercontent.com/python-visualization/folium/master/examples/data'
us_states = f'{url}/us-states.json'

geo_json_data = json.loads(requests.get(us_states).text)

In [555]:
geo_json_data

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'id': 'AL',
   'properties': {'name': 'Alabama'},
   'geometry': {'type': 'Polygon',
    'coordinates': [[[-87.359296, 35.00118],
      [-85.606675, 34.984749],
      [-85.431413, 34.124869],
      [-85.184951, 32.859696],
      [-85.069935, 32.580372],
      [-84.960397, 32.421541],
      [-85.004212, 32.322956],
      [-84.889196, 32.262709],
      [-85.058981, 32.13674],
      [-85.053504, 32.01077],
      [-85.141136, 31.840985],
      [-85.042551, 31.539753],
      [-85.113751, 31.27686],
      [-85.004212, 31.003013],
      [-85.497137, 30.997536],
      [-87.600282, 30.997536],
      [-87.633143, 30.86609],
      [-87.408589, 30.674397],
      [-87.446927, 30.510088],
      [-87.37025, 30.427934],
      [-87.518128, 30.280057],
      [-87.655051, 30.247195],
      [-87.90699, 30.411504],
      [-87.934375, 30.657966],
      [-88.011052, 30.685351],
      [-88.10416, 30.499135],
      [-88.137022, 30.318396],
    